In [1]:
import pandas as pd
import numpy as np
from tqdm import tqdm
import logging
import sys
import json
import datetime
import itertools
import datetime

import pyexasol
from citymobil_python_mysql_wrapper import MysqlWrapper
from citymobil_python_clickhouse_wrapper import ClickHouseWrapper

In [2]:
cred = pd.read_json(r'/Users/skostuchik/crd_exa.json')
user = cred.iloc[0, 0]
password = cred.iloc[0, 1]
mysql_password = cred.iloc[0, 2]
ch_password = cred.password_ch.squeeze()

In [3]:
pd.options.display.max_rows = 999
pd.options.display.max_columns = 999

In [4]:
%%capture
logging.basicConfig(stream=sys.stdout, level=logging.DEBUG)
logger = logging.getLogger()

# initialize connect to MySQL Test
mysql_99 = MysqlWrapper(
    logger,
    "192.168.63.99",
    3306,
    user,
    mysql_password,
    "city"
)

mysql_85 = MysqlWrapper(
    logger,
    "192.168.50.85",
    3306,
    user,
    mysql_password,
    "city"
)

# initialize connect to ClickHouse
clickhouse_chbi = ClickHouseWrapper(
    logger,
    url="chbi1.stl.msk.city-srv.ru:8123",
    user=user,
    password=ch_password,
    create_and_assign_event_loop=False,  # for django threads with no event loop
    allow_nested_event_loops=True  # for jupyter threads with existed event loop
)

clickhouse_vip = ClickHouseWrapper(
    logger,
    url="http://chmain-vip.city-srv.tech:8123",
    user=user,
    password=password,
    create_and_assign_event_loop=False,  # for django threads with no event loop
    allow_nested_event_loops=True  # for jupyter threads with existed event loop
)

#Exasol
C = pyexasol.connect(dsn='ex1..3.city-srv.ru:8563', user=user, password=password, fetch_dict=True)

In [116]:
query_views_esaxol = '''
select ca.locality_rk,
     to_date(VIEW_DTTM) as dt,
     SUM(VIEW_FIFTEEN_MIN_CNT)  as views
FROM REPLICA_MART.CALCULATION_AGGREGATED ca
WHERE VIEW_DTTM >= '2020-04-01 00:00:00'
    and ca.LOCALITY_RK in (22534)
    --and ca.TARIFF_RK in (3438)
GROUP BY 1, 2
'''


query_drivers_esaxol = '''
SELECT oc.MAIN_ID_LOCALITY locality_rk,
    to_date(add_seconds(oc.ORDEREDDATE,coalesce(gl.time_offset,0))) dt,
    COUNT( distinct oc.Driver) as drivers
FROM replica.order_closed oc
    inner join dds.s_company_account cmp1
        on oc.companyid = cmp1.company_account_rk
        and oc.ordereddate >=  cmp1.valid_from_dttm
        and oc.ordereddate < cmp1.valid_to_dttm
    left join md.locality gl
        on oc.main_id_locality = gl.locality_rk
WHERE oc.ORDEREDDATE >= '2020-04-01 00:00:00'
    and oc.MAIN_ID_LOCALITY in (22534)
    --and oc.TARIFF in (3438)
    AND oc.COMPANYID in (1, 5810, 5918)
    AND oc.g_type = 0 /*Исключаем тестовые заказа*/
    AND oc.get_company <> 3 /*Тестовая компания*/
    AND cmp1.company_rk = 1 /*Платформа -Ситимобил*/
    AND oc.DRIVER > 0 /* Исключаем заказы с неназначенным водителем */
group by 1, 2
order by 1, 2
'''

In [7]:
# drivers_views_sql = '''
# select t.locality_rk,
#      DAYOFWEEK(date) wd,
#      toDate(dt) dt,
#      max(open_drivers_corrected) as drivers,
#      max(sum_uViews)             as uViews
# from surge_statistic.surge_20_data s
#        join exasol_mart.tariff t on toUInt64(s.tariff_id) = toUInt64(t.tariff_rk)
# where 1 = 1
#     and date >= toDate('2020-05-01') and date <= toDate('2021-12-08')
#     and t.locality_rk = 22534
#     and t.tariff_group_rk in (2, 3, 4, 5)
# group by t.locality_rk, wd, dt
# '''

In [8]:
# views_sql = '''
# select t2.locality_id,
#        t2.date_day,
#        t2.views,
#        t2.created_date
# from(
# select locality_id, version, date_day, max(created_date) as created_date
# from segmentation.forecast_views_daily
# where 1=1
# group by locality_id, version,  date_day) as t
# join segmentation.forecast_views_daily t2 on t.created_date = t2.created_date
#                                                   and t.date_day = t2.date_day
#                                                   and t.version = t2.version
#                                                   and t.locality_id = t2.locality_id
# where t2.locality_id=22534
#       and t2.version = 'prophet_06'
# '''

# drivers_sql = '''
# select t2.locality_id,
#        t2.date_day,
#        t2.drivers,
#        t2.created_date
# from(
# select locality_id, version, date_day, max(created_date) as created_date
# from segmentation.forecast_drivers_daily
# where 1=1
# group by locality_id, version,  date_day) as t
# join segmentation.forecast_drivers_daily t2 on t.created_date = t2.created_date
#                                                   and t.date_day = t2.date_day
#                                                   and t.version = t2.version
#                                                   and t.locality_id = t2.locality_id
# where t2.locality_id=22534
#       and t2.version = 'prophet_06'
# '''

In [9]:
# open_ref_sql = '''
# select date,
#        avg(open_ref)                             as open_ref,
#        avg(openref_timetable_v2_uo2da_ref_val)   as openref_timetable_v2_uo2da_ref_val,
#        avg(openref_timetable_v2_step_pos_val)    as openref_timetable_v2_step_pos_val,
#        avg(openref_timetable_v2_step_neg_val)    as openref_timetable_v2_step_neg_val,
#        avg(openref_timetable_v2_min_openref_val) as openref_timetable_v2_min_openref_val,
#        avg(openref_timetable_v2_max_openref_val) as openref_timetable_v2_max_openref_val
# from (
#       select date,
#              trim(visitParamExtractRaw(surge_config, 'openref_timetable_v2')) as openref_timetable_v2,
#              trim(visitParamExtractRaw(
#                      replaceAll(
#                              openref_timetable_v2,
#                              '\\', ''),
#                      'uo2da_ref'))                                            as openref_timetable_v2_uo2da_ref,
#              toFloat64(
#                      if(empty(openref_timetable_v2_uo2da_ref), '0.0',
#                         ifNull(openref_timetable_v2_uo2da_ref, '0.0'))
#                  )                                                            as openref_timetable_v2_uo2da_ref_val,


#              trim(visitParamExtractRaw(
#                      replaceAll(
#                              openref_timetable_v2,
#                              '\\', ''),
#                      'step_pos'))                                             as openref_timetable_v2_step_pos,
#              toFloat64(
#                      if(empty(openref_timetable_v2_step_pos), '0.0',
#                         ifNull(openref_timetable_v2_step_pos, '0.0'))
#                  )                                                            as openref_timetable_v2_step_pos_val,

#              trim(visitParamExtractRaw(
#                      replaceAll(
#                              openref_timetable_v2,
#                              '\\', ''),
#                      'step_neg'))                                             as openref_timetable_v2_step_neg,
#              toFloat64(
#                      if(empty(openref_timetable_v2_step_neg), '0.0',
#                         ifNull(openref_timetable_v2_step_neg, '0.0'))
#                  )                                                            as openref_timetable_v2_step_neg_val,


#              trim(visitParamExtractRaw(
#                      replaceAll(
#                              openref_timetable_v2,
#                              '\\', ''),
#                      'min_openref'))                                          as openref_timetable_v2_min_openref,

#              toFloat64(
#                      if(empty(openref_timetable_v2_min_openref), '0.0',
#                         ifNull(openref_timetable_v2_min_openref, '0.0'))
#                  )                                                            as openref_timetable_v2_min_openref_val,

#              trim(visitParamExtractRaw(
#                      replaceAll(
#                              openref_timetable_v2,
#                              '\\', ''),
#                      'max_openref'))                                          as openref_timetable_v2_max_openref,
#              toFloat64(
#                      if(empty(openref_timetable_v2_max_openref), '0.0',
#                         ifNull(openref_timetable_v2_max_openref, '0.0'))
#                  )                                                            as openref_timetable_v2_max_openref_val,

#              toFloat64(
#                      replaceAll(if(
#                                         empty(
#                                                 trim(visitParamExtractRaw(surge_config, 'open_ref'))
#                                             ),
#                                         '0.0',
#                                         ifNull(trim(visitParamExtractRaw(surge_config, 'open_ref')),
#                                                '0.0')
#                                     ), '"', '')
#                  )
#                                                                               as open_ref
#       from surge_statistic.surge_20_data base_data
#                global all
#                inner join (select id, admin_name
#                            from mysql('192.168.50.151:3306', 'city', 'tariff1',
#                                       'etlupload',
#                                       'Nah7Aik5')
#                            where companyid in (1, 5810)
#                              and id_locality in (22534)
#                              and show = 1) tariff1
#                           ON toUInt64(tariff1.id) = toUInt64(base_data.tariff_id)
#       where dt >= '2021-07-07'
#         and test_id in [8243]
#          )
# group by date
# '''

In [124]:
driver_bonus_sql = '''
    select id_locality, segment_type, weekdays, date_start, IFNULL(date(date_end), '2022-01-01') date_end,
    settings, period
    from driver_bonus
    where date(date_start) >= '2020-04-01'
        and id_locality = 22534
'''

driver_bonus_order_counts_sql = '''
    select date(recalculated_date) date_day, sum(count) orders_counted, sum(fraud_count) fraud_counted, sum(ifnull(paid_sum, 0)) paid_sum
    from driver_bonus_order_counts
    where bonus_id in (
        select id
        from driver_bonus
        where date(date_start) >= '2020-04-01'
            and id_locality = 22534)
    group by date(recalculated_date)
'''

In [125]:
pricing_sql_1 = '''
    select bit_index, dow, t.*
    from (
        select bit_index, dow,
            case
                when bit_index = 15 and dow in (1, 2, 3, 4) then 1
                when bit_index = 16 and dow in (5) then 1
                when bit_index = 30 and dow in (2, 3, 4, 5) then 1
                when bit_index = 31 and dow in (1, 2, 3, 4, 5) then 1
                when bit_index = 60 and dow in (3, 4, 5, 6) then 1
                when bit_index = 67 and dow in (1, 2, 7) then 1
                when bit_index = 96 and dow in (6, 7) then 1
                when bit_index = 97 and dow in (1, 6, 7) then 1
                when bit_index = 127 and dow in (1, 2, 3, 4, 5, 6, 7) then 1
            end is_ok
        from (
            select
                @num:=@num+1 bit_index
            from
                tariff_times1_history,
                (select @num:=-1) num
            limit
                127) v
        cross join (
            select
                @nu:=@nu+1 dow
            from
                tariff_times1_history,
                (select @nu:=-1) num
            limit
                127) v2) dow
    left join (
        select date(created_at) created_at, IFNULL(date(deleted_at), '2022-01-01') deleted_at,
               time_begin, time_end,
               case
                   when time_end < time_begin
                       then time_to_sec(date_add(TIMEDIFF(date_add(time_end, interval 1 day), time_begin), interval 1 second)) / (3600)
                   else time_to_sec(date_add(TIMEDIFF(time_end, time_begin), interval 1 second)) / (3600)
                   end time_duration,
               days, price, min_price,
               prepaid_time, prepaid_way, price_time, price_time_taximeter, free_waiting_time, waiting_price,
               driver_min_price, price_way, price_way_taximeter, waiting_price_taximeter, paid_cancellation_price,
               driver_gold_min_price, driver_silver_min_price, paid_waiting_for_driver
        from tariff_times1_history
        where id_tariff in (
            select id
            from tariff1
            where id_locality = 22534)
        ) t on t.days = dow.bit_index
    where is_ok = 1
'''

In [126]:
gch_sql = '''
select to_date(time_start) time_start, NVL(to_date(time_end), '2022-01-01') time_end, week_day,
       driver_min_price, nvl(client_extra_charge, 0) client_extra_charge
from replica.geominimal_change_history gch
where id_locality = 22534
 and DRIVER_MIN_PRICE is not null
'''

In [127]:
dsl_sql = '''
    select
           case when IDS_PRIORITY_LEVEL LIKE '%3%' then 1 else 0 end is_gold,
           DATE_START, DATE_END, STAIRS
    from replica.driver_surcharge_list
    where id_locality = 22534
'''

dsp_sql = '''
    select "DATE", sum(ORDERS_COUNT) ORDERS_COUNT, sum(FEE) fee
    from replica.driver_surcharge_payments
    where SURCHARGE_ID in (
        select id
        from replica.driver_surcharge_list
        where id_locality = 22534)
        and "DATE" >= '2020-04-01'
    group by "DATE"
'''

In [128]:
coupon_list_sql = '''
    SELECT to_date(DATE_START) DATE_START, to_date(DATE_END) DATE_END, MAX_USAGE_COUNT, MIN_PRICE,
    TARIFFS, MAX_DISCOUNT
    FROM REPLICA.COUPON_LIST cl
    where 1=1
          and (name like '%VRN%')
'''

coupon_results_sql = '''
    SELECT to_date(o.ORDER_DTTM) dt, count(distinct ic.DISCOUNT_COUPON_ID) unique_coupons, sum(ic.CI_COUPONS) CI_COUPONS,
           count(ORDER_RK) COUPONS_ORDERS
    from EMART."ORDER" o
    join REPLICA_MART.INCENTIVE_COMISSION as ic on ic.ORDER_ID = o.ORDER_RK and ic.DISCOUNT_COUPON_ID > 0
    where to_date(o.ORDER_DTTM) >= '2020-04-01'
        and o.LOCALITY_RK = 22534
    group by 1
'''

In [129]:
y_sql = '''
select to_date(o.ORDER_DTTM) dt, count(o.ORDER_RK) orders, sum(o.STATUS_CD='CP') rides,
       local.rides / local.orders o2r,
       sum(o.CLIENT_BILL_AMT) CLIENT_BILL_AMT,
       sum(case
            when o.status_cd='CP' and coalesce(corp.billing_type,1) != 2
                then ic.commission_total_amt - ic.di_total_amt - ic.ci_total_amt
            when o.status_cd='CP' and corp.billing_type = 2
               then
                ic.client_bill_amt + ic.ci_paid_partner + ic.ci_hr /*итоговый клиентский чек, с учетом доплат парнетра и наших HR-доплат */
                - (
                    ic.driver_bill_amt /*Сумма водительского чека. Включает в себя di_geo_minimal_amt и di_minimal*/
                    + ic.di_welcome_dxgy + ic.di_power_dxgy + ic.di_other_dxgy + ic.di_main_dxgy  /* DxGy */
                    + ic.di_mfg /* MFG */
                    + ic.di_guaranteed_amt_per_hour /* Geominimal */
                   )
                + ic.commission_total_amt /*итоговая комиссия */
       end) contribution
from emart.order o
left join replica_mart.incentive_comission ic
    on o.order_rk = ic.order_id
left join replica.corporation corp
    on o.corporation_rk = corp.id
where
    o.local_order_dttm between '2020-04-01' and '2021-12-08'
    and o.order_company_rk = 1 /*компания, распределившая заказ cитимобил*/
    and o.tariff_zone_nm not like 'Чикаго%'
    and lower(o.tariff_group_nm) not in ('самокаты')
    and o.LOCALITY_RK = 22534
group by 1
'''

In [130]:
voronezh_tariff_sql = '''
    select id,
           row_number() over () rn
    from replica.TARIFF1
    where ID_LOCALITY = 22534
'''

In [131]:
#views_data, drivers_data = mysql_99.fetch(views_sql), mysql_99.fetch(drivers_sql)
#drivers_views = clickhouse_vip.fetch(drivers_views_sql)

In [132]:
#drivers_views = drivers_views[['locality_rk', 'wd', 'dt', 'drivers', 'uViews']]

In [133]:
#drivers_views.rename(columns={'dt':'date_day'}, inplace=True)

In [134]:
#drivers_views['date_day'].min()

In [135]:
views = pd.DataFrame(C.execute(query_views_esaxol).fetchall())
drivers = pd.DataFrame(C.execute(query_drivers_esaxol).fetchall())

In [136]:
drivers_views = drivers.merge(views, how='left', on=['LOCALITY_RK', 'DT'])

In [137]:
drivers_views['DT'] = drivers_views['DT'].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%d").date())

In [138]:
drivers_views['wd'] = drivers_views['DT'].apply(lambda x: x.isoweekday())

In [139]:
drivers_views.rename(columns={'DT':'date_day'}, inplace=True)

In [140]:
#open_ref_data = clickhouse.fetch(open_ref_sql)
#open_ref_data = pd.read_csv('/Users/skostuchik/projects/various_files/csv_all_all_surge_part.csv')

In [141]:
#open_ref_data['date_day'] = open_ref_data['date'].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%d").date())

In [142]:
driver_bonus = mysql_85.fetch(driver_bonus_sql)
driver_bonus_order_counts = mysql_85.fetch(driver_bonus_order_counts_sql)

In [143]:
pricing = mysql_85.fetch(pricing_sql_1)

In [144]:
pricing['deleted_at'] = pricing['deleted_at'].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%d").date())

In [145]:
gch = pd.DataFrame(C.execute(gch_sql).fetchall())

In [146]:
for c in ['TIME_START', 'TIME_END']:
    gch[c] = gch[c].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%d").date())

In [147]:
dsl = pd.DataFrame(C.execute(dsl_sql).fetchall())
dsp = pd.DataFrame(C.execute(dsp_sql).fetchall())

In [148]:
dsp.rename(columns={'DATE':'date_day'}, inplace=True)

In [149]:
dsp['date_day'] = dsp['date_day'].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%d").date())

In [150]:
coupon_results = pd.DataFrame(C.execute(coupon_results_sql).fetchall())
coupon_list = pd.DataFrame(C.execute(coupon_list_sql).fetchall())

In [151]:
coupon_results['DT'] = coupon_results['DT'].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%d").date())
for c in ['DATE_START', 'DATE_END']:
    coupon_list[c] = coupon_list[c].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%d").date())

In [152]:
coupon_results.rename(columns={'DT':'date_day'}, inplace=True)

In [153]:
y = pd.DataFrame(C.execute(y_sql).fetchall())

In [154]:
y['DT'] = y['DT'].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%d").date())
y.rename(columns={'DT':'date_day'}, inplace=True)

In [155]:
voronezh_tariff = pd.DataFrame(C.execute(voronezh_tariff_sql).fetchall())

In [156]:
tariff_dict = {r.ID:r.RN for i, r in voronezh_tariff.iterrows()}

In [157]:
dt_data = pd.DataFrame(list(itertools.product(list(pd.date_range(start='4/1/2020', end='12/8/2021', freq='D')),
                                              [22534])), columns=['date_day','LOCALITY_RK'])
dt_data['dow'] = dt_data['date_day'].apply(lambda x: x.isoweekday())

In [158]:
dt_data['date_day'] = dt_data['date_day'].apply(lambda x: x.date())

# DI

In [159]:
def safe_list_get(l, idx, default={}):
    try:
        return l[idx]
    except:
        return default

In [160]:
db_data = pd.DataFrame()
for t in tqdm(driver_bonus.itertuples()):
    for wd in json.loads(t.weekdays):
        settings_list = {}
        settings_list.update({'LOCALITY_RK':t.id_locality, 'WD':wd,
                             'date_start':t.date_start.date(), 'date_end':pd.Timestamp(t.date_end).date(),
                             'period':t.period, 'segment_type':t.segment_type,
                             'polygons':json.loads(t.settings).get('polygons')})

        for i in range(3):
            #print(safe_list_get(json.loads(t.settings).get('splits'), i).get('targets'))
            if safe_list_get(json.loads(t.settings).get('splits'), i).get('targets')==None:
                settings = [{'target': '0', 'total_payment': '0', 'personal_target': '', 'one_ride_payment': ''}]
            else:
                settings = (safe_list_get(json.loads(t.settings).get('splits'), i).get('targets'))
            settings_list.update({f'target_{i}':settings[0].get('target'),
                                  f'payment_{i}':settings[0].get('total_payment')})

        db_data = db_data.append(settings_list, ignore_index=True)
        
for c in ['LOCALITY_RK', 'WD', 'period', 'segment_type']:
    db_data[c] = db_data[c].astype(int)

247it [00:06, 36.80it/s]


In [161]:
db_data['polygons'] = db_data['polygons'].apply(lambda x: 0 if x==None else 1)

In [162]:
db_data = dt_data.merge(db_data, how='left', left_on=['LOCALITY_RK','dow'], right_on=['LOCALITY_RK','WD'])

In [163]:
db_data = db_data[(db_data['date_day']>=db_data['date_start'])&
                  (db_data['date_day']<=db_data['date_end'])].drop(['date_start','date_end','dow'], axis = 1)

In [164]:
for c in ['target_0','target_1','target_2','payment_0','payment_1','payment_2']:
    db_data[c] = db_data[c].astype(int)

In [165]:
db_data_agg = db_data.groupby(['LOCALITY_RK','date_day'])[
    'target_0', 'target_1', 'target_2', 'payment_0', 'payment_1', 'payment_2'].mean().reset_index()

<ipython-input-165-1a92bf824530>:1: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  db_data_agg = db_data.groupby(['LOCALITY_RK','date_day'])[


<b>MFG</b>

In [166]:
dsl_df = pd.DataFrame()
for i, r in dsl.iterrows():
    k_max, v_max = 0, 0
    for k, v in json.loads(r.STAIRS)[0].get('steps').items():
        k, v = int(k), int(v)
        if k > k_max:
            k_max = k
        if v > v_max:
            v_max = v
    dsl_df = dsl_df.append({'IS_GOLD':r.IS_GOLD, 'DATE_START':r.DATE_START, 'DATE_END':r.DATE_END, 
                            'max_stair':k_max, 'max_fare':v_max}, ignore_index=True)

In [167]:
for c in ['DATE_END', 'DATE_START']:
    dsl_df[c] = dsl_df[c].apply(lambda x: datetime.datetime.strptime(x, "%Y-%m-%d").date())

In [168]:
cj_dsl = dt_data.merge(dsl_df, how='cross')
cj_dsl = cj_dsl[(cj_dsl['date_day']>=cj_dsl['DATE_START'])&(cj_dsl['date_day']<=cj_dsl['DATE_END'])].drop(
    ['dow', 'DATE_END', 'DATE_START'], axis=1)

In [169]:
cj_dsl_gold = cj_dsl[cj_dsl['IS_GOLD']==1].groupby('date_day')[['max_fare','max_stair']].median().reset_index()
cj_dsl_not_gold = cj_dsl[cj_dsl['IS_GOLD']==0].groupby('date_day')[['max_fare','max_stair']].median().reset_index()

In [170]:
dsl_data = dt_data.merge(cj_dsl_gold, how='left', on='date_day').merge(
    cj_dsl_not_gold, how='left', on='date_day', suffixes=["_gold", "_not_gold"])

<b>Geominimal</b>

In [171]:
cj_gch = dt_data.merge(gch, how='cross')

In [172]:
gch_data = cj_gch[(cj_gch['dow']==cj_gch['WEEK_DAY'])&(cj_gch['date_day']>=cj_gch['TIME_START'])&
                  (cj_gch['date_day']<=cj_gch['TIME_END'])].drop(
    ['dow','TIME_START','TIME_END','WEEK_DAY'], axis=1).groupby('date_day').median().reset_index()

In [173]:
db_data_f = db_data_agg.merge(driver_bonus_order_counts, how='left', on='date_day')

In [174]:
db_data_f.columns = ['driver_bonus_'+c if c!='date_day' else c
                     for c in db_data_f.columns]
dsl_data.columns = ['mfg_'+c if c!='date_day' else c for c in dsl_data.columns]
dsp.columns = ['mfg_'+c if c!='date_day' else c for c in dsp.columns]
gch_data.columns = ['geomin_'+c if c!='date_day' else c for c in gch_data.columns]

In [175]:
di_df = db_data_f.merge(
    dsl_data, how='left', on='date_day').merge(dsp, how='left', on='date_day').merge(
    gch_data, how='left', on='date_day').fillna(0)

In [176]:
di_df = di_df.drop(['mfg_LOCALITY_RK', 'mfg_dow','geomin_LOCALITY_RK'], axis=1).rename(
    columns={'driver_bonus_LOCALITY_RK':'LOCALITY_RK'})

In [177]:
di_df

LOCALITY_RK    date_day  driver_bonus_target_0  driver_bonus_target_1  \
0          22534  2020-04-07               0.000000               0.000000   
1          22534  2020-04-08               0.000000               0.000000   
2          22534  2020-04-15             140.000000               0.000000   
3          22534  2020-04-16             140.000000               0.000000   
4          22534  2020-04-17             140.000000               0.000000   
5          22534  2020-04-18             140.000000               0.000000   
6          22534  2020-04-19             140.000000               0.000000   
7          22534  2020-04-20             140.000000               0.000000   
8          22534  2020-04-21             140.000000               0.000000   
9          22534  2020-04-22             140.000000               0.000000   
10         22534  2020-04-23             140.000000               0.000000   
11         22534  2020-04-24             140.000000               0.000000   
12         22534  2020-04-25             140.000000               0.000000   
13         22534  2020-04-26             120.000000               0.000000   
14         22534  2020-04-27             120.000000               0.000000   
15         22534  2020-04-28             120.000000               0.000000   
16         22534  2020-04-29             120.000000               0.000000   
17         22534  2020-04-30             120.000000               0.000000   
18         22534  2020-05-01             120.000000               0.000000   
19         22534  2020-05-02             120.000000               0.000000   
20         22534  2020-05-03             120.000000               0.000000   
21         22534  2020-05-04             120.000000               0.000000   
22         22534  2020-05-05             120.000000               0.000000   
23         22534  2020-05-06             120.000000               0.000000   
24         22534  2020-05-07             120.000000               0.000000   
25         22534  2020-05-08             120.000000               0.000000   
26         22534  2020-05-09             120.000000               0.000000   
27         22534  2020-05-10             120.000000               0.000000   
28         22534  2020-05-11             120.000000               0.000000   
29         22534  2020-05-12             120.000000               0.000000   
30         22534  2020-05-13             120.000000               0.000000   
31         22534  2020-05-14             120.000000               0.000000   
32         22534  2020-05-15             120.000000               0.000000   
33         22534  2020-05-16             120.000000               0.000000   
34         22534  2020-05-17             120.000000               0.000000   
35         22534  2020-05-18             120.000000               0.000000   
36         22534  2020-05-19             103.333333               0.000000   
37         22534  2020-05-20             103.333333               0.000000   
38         22534  2020-05-21             103.333333               0.000000   
39         22534  2020-05-22             103.333333               0.000000   
40         22534  2020-05-23              95.000000               0.000000   
41         22534  2020-05-24              95.000000               0.000000   
42         22534  2020-05-25              95.000000               0.000000   
43         22534  2020-05-26              82.857143               0.000000   
44         22534  2020-05-27              82.857143               0.000000   
45         22534  2020-05-28              82.857143               0.000000   
46         22534  2020-05-29              82.857143               0.000000   
47         22534  2020-05-30              82.857143               0.000000   
48         22534  2020-05-31              82.857143               0.000000   
49         22534  2020-06-01              82.857143               0.000000   
50         22534  2020-06-0

# CI

In [178]:
def tariff_parser(x):
    s = 0
    for i in json.loads(x):
        if tariff_dict.get(i):
            s += 2**tariff_dict.get(i)
        else:
            continue
        
    return(s)

In [179]:
coupon_list['coupon_tariff_bitmap'] = coupon_list['TARIFFS'].apply(tariff_parser)
coupon_list.drop('TARIFFS', axis=1, inplace=True)

In [180]:
cj_coupon_list = dt_data.merge(coupon_list, how='cross')
cj_coupon_list = cj_coupon_list[(cj_coupon_list['date_day']>=cj_coupon_list['DATE_START'])
                                &(cj_coupon_list['date_day']<=cj_coupon_list['DATE_END'])]

In [181]:
cj_coupon_list = cj_coupon_list.drop(['dow', 'DATE_START', 'DATE_END'], axis=1).groupby(
    'date_day').median().reset_index()

In [182]:
ci_coupones = dt_data.merge(cj_coupon_list, how='left', on='date_day').merge(
    coupon_results, how='left', on='date_day')

In [183]:
ci_coupones

date_day  LOCALITY_RK_x  dow  LOCALITY_RK_y  MAX_USAGE_COUNT  \
0    2020-04-01          22534    3        22534.0             10.0   
1    2020-04-02          22534    4        22534.0             10.0   
2    2020-04-03          22534    5        22534.0             10.0   
3    2020-04-04          22534    6        22534.0             10.0   
4    2020-04-05          22534    7        22534.0             10.0   
5    2020-04-06          22534    1        22534.0             10.0   
6    2020-04-07          22534    2        22534.0             10.0   
7    2020-04-08          22534    3        22534.0             10.0   
8    2020-04-09          22534    4        22534.0             10.0   
9    2020-04-10          22534    5        22534.0             10.0   
10   2020-04-11          22534    6        22534.0             10.0   
11   2020-04-12          22534    7        22534.0             10.0   
12   2020-04-13          22534    1        22534.0             10.0   
13   2020-04-14          22534    2        22534.0             10.0   
14   2020-04-15          22534    3        22534.0             10.0   
15   2020-04-16          22534    4        22534.0             10.0   
16   2020-04-17          22534    5        22534.0             10.0   
17   2020-04-18          22534    6        22534.0             10.0   
18   2020-04-19          22534    7        22534.0             10.0   
19   2020-04-20          22534    1        22534.0             10.0   
20   2020-04-21          22534    2        22534.0             10.0   
21   2020-04-22          22534    3        22534.0             10.0   
22   2020-04-23          22534    4        22534.0             10.0   
23   2020-04-24          22534    5        22534.0             10.0   
24   2020-04-25          22534    6        22534.0             10.0   
25   2020-04-26          22534    7        22534.0             10.0   
26   2020-04-27          22534    1        22534.0             10.0   
27   2020-04-28          22534    2        22534.0             10.0   
28   2020-04-29          22534    3        22534.0              2.0   
29   2020-04-30          22534    4        22534.0              2.0   
30   2020-05-01          22534    5        22534.0              2.0   
31   2020-05-02          22534    6        22534.0              2.0   
32   2020-05-03          22534    7        22534.0              2.0   
33   2020-05-04          22534    1        22534.0              2.0   
34   2020-05-05          22534    2        22534.0              2.0   
35   2020-05-06          22534    3        22534.0              2.0   
36   2020-05-07          22534    4        22534.0              6.0   
37   2020-05-08          22534    5        22534.0              2.0   
38   2020-05-09          22534    6        22534.0              2.0   
39   2020-05-10          22534    7        22534.0              2.0   
40   2020-05-11          22534    1        22534.0              2.0   
41   2020-05-12          22534    2        22534.0              2.0   
42   2020-05-13          22534    3        22534.0              2.0   
43   2020-05-14          22534    4        22534.0              2.0   
44   2020-05-15          22534    5        22534.0              2.0   
45   2020-05-16          22534    6        22534.0              5.5   
46   2020-05-17          22534    7        22534.0              5.5   
47   2020-05-18          22534    1        22534.0              5.5   
48   2020-05-19          22534    2        22534.0              5.5   
49   2020-05-20          22534    3        22534.0              5.5   
50   2020-05-21          22534    4        22534.0              5.5   
51   2020-05-22          22534    5        22534.0              5.5   
52   2020-05-23          22534    6        22534.0              3.0   
53   2020-05-24          22534    7        22534.0              3.0   
54   2020-05-25          22534    1        22534.0              3.0   
55   2020-05-26          22534 

# Pricing

In [184]:
cj_pricing = dt_data.merge(pricing, how='cross')

In [185]:
cj_pricing = cj_pricing[(cj_pricing['dow_x']==cj_pricing['dow_y'])&
                        (cj_pricing['date_day']>=cj_pricing['created_at'])&
                        (cj_pricing['date_day']<=cj_pricing['deleted_at'])]

In [186]:
cj_pricing = cj_pricing.drop(['dow_x','bit_index','dow_y','created_at','deleted_at','time_begin',
                              'time_end','days','price'], axis = 1)

In [187]:
for c in cj_pricing.columns.tolist()[2:]:
    cj_pricing[f'{c}_prod'] = np.multiply(cj_pricing[c], cj_pricing['time_duration'])

In [188]:
cj_pricing = cj_pricing.groupby('date_day')['time_duration', 'min_price_prod', 'prepaid_time_prod',
                               'prepaid_way_prod', 'price_time_prod', 'price_time_taximeter_prod',
                               'free_waiting_time_prod', 'waiting_price_prod', 'driver_min_price_prod',
                               'price_way_prod', 'price_way_taximeter_prod', 'waiting_price_taximeter_prod',
                               'paid_cancellation_price_prod', 'driver_gold_min_price_prod',
                               'driver_silver_min_price_prod', 'paid_waiting_for_driver_prod'].sum().reset_index()

<ipython-input-188-23923315af74>:1: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  cj_pricing = cj_pricing.groupby('date_day')['time_duration', 'min_price_prod', 'prepaid_time_prod',


In [189]:
for c in cj_pricing.columns.tolist()[2:]:
    new = c.replace('prod','weighted')
    cj_pricing[new] = cj_pricing[c] / cj_pricing['time_duration']
    cj_pricing[new] = cj_pricing[new].astype(int)

In [190]:
cj_pricing = cj_pricing[['date_day', 'min_price_weighted',
       'prepaid_time_weighted', 'prepaid_way_weighted', 'price_time_weighted',
       'price_time_taximeter_weighted', 'free_waiting_time_weighted',
       'waiting_price_weighted', 'driver_min_price_weighted',
       'price_way_weighted', 'price_way_taximeter_weighted',
       'waiting_price_taximeter_weighted', 'paid_cancellation_price_weighted',
       'driver_gold_min_price_weighted', 'driver_silver_min_price_weighted',
       'paid_waiting_for_driver_weighted']]

In [191]:
cj_pricing

date_day  min_price_weighted  prepaid_time_weighted  \
0    2020-05-12                  51                      4   
1    2020-05-13                  53                      5   
2    2020-05-14                  53                      5   
3    2020-05-15                  53                      5   
4    2020-05-18                  53                      5   
5    2020-05-19                  53                      5   
6    2020-05-20                  53                      5   
7    2020-05-21                  53                      5   
8    2020-05-22                  53                      5   
9    2020-05-25                  53                      5   
10   2020-05-26                  53                      5   
11   2020-05-27                  53                      5   
12   2020-05-28                  53                      5   
13   2020-05-29                  53                      5   
14   2020-06-01                  53                      5   
15   2020-06-02                  53                      5   
16   2020-06-03                  53                      5   
17   2020-06-04                  53                      5   
18   2020-06-05                  53                      5   
19   2020-06-08                  53                      5   
20   2020-06-09                  53                      5   
21   2020-06-10                  53                      5   
22   2020-06-11                  53                      5   
23   2020-06-12                  53                      5   
24   2020-06-15                  53                      5   
25   2020-06-16                  53                      5   
26   2020-06-17                  53                      5   
27   2020-06-18                  53                      5   
28   2020-06-19                  53                      5   
29   2020-06-22                  53                      5   
30   2020-06-23                  53                      5   
31   2020-06-24                  53                      5   
32   2020-06-25                  53                      5   
33   2020-06-26                  53                      5   
34   2020-06-29                  53                      5   
35   2020-06-30                  53                      5   
36   2020-07-01                  53                      5   
37   2020-07-02                  53                      5   
38   2020-07-03                  53                      5   
39   2020-07-06                  53                      5   
40   2020-07-07                  53                      5   
41   2020-07-08                  53                      5   
42   2020-07-09                  53                      5   
43   2020-07-10                  53                      5   
44   2020-07-13                  53                      5   
45   2020-07-14                  53                      5   
46   2020-07-15                  53                      5   
47   2020-07-16                  53                      5   
48   2020-07-17                  53                      5   
49   2020-07-20                  53                      5   
50   2020-07-21                  53                      5   
51   2020-07-22                  55                      5   
52   2020-07-23                  54                      5   
53   2020-07-24                  54                      5   
54   2020-07-25                  59                      5   
55   2020-07-26                  59                      5   
56   2020-07-27                  54                      5   
57   2020-07-28                  54                      5   
58   2020-07-29                  54                      5   
59   2020-07-30                  54                      5   
60   2020-07-31                  54                      5   
61   2020-08-01                  59                      5   
62   2020-08-02                  59                      5   
63   2020-08-03                  54    

# Insert Into Sandbox

In [192]:
#df = views_data.merge(drivers_data[['date_day','drivers']], on='date_day', how='left').drop(['created_date'], axis=1)

In [193]:
#df = df.merge(open_ref_data, how='left', on='date_day').drop('date', axis=1)

In [204]:
df = drivers_views.merge(di_df, how='left', on=['date_day','LOCALITY_RK'])

In [196]:
#df = df.merge(di_df, how='left', on='date_day')

In [207]:
df = df.merge(cj_pricing, how='left', on='date_day')

In [210]:
df = df.merge(ci_coupones.drop(['dow'], axis=1), how='left', on='date_day')

In [213]:
df = df.merge(y, how='left', on='date_day')

In [215]:
df = df.sort_values(by='date_day').fillna(0)

In [216]:
df.columns

Index(['LOCALITY_RK', 'date_day', 'DRIVERS', 'VIEWS', 'wd',
       'driver_bonus_target_0', 'driver_bonus_target_1',
       'driver_bonus_target_2', 'driver_bonus_payment_0',
       'driver_bonus_payment_1', 'driver_bonus_payment_2',
       'driver_bonus_orders_counted', 'driver_bonus_fraud_counted',
       'driver_bonus_paid_sum', 'mfg_max_fare_gold', 'mfg_max_stair_gold',
       'mfg_max_fare_not_gold', 'mfg_max_stair_not_gold', 'mfg_ORDERS_COUNT',
       'mfg_FEE', 'geomin_DRIVER_MIN_PRICE', 'geomin_CLIENT_EXTRA_CHARGE',
       'min_price_weighted', 'prepaid_time_weighted', 'prepaid_way_weighted',
       'price_time_weighted', 'price_time_taximeter_weighted',
       'free_waiting_time_weighted', 'waiting_price_weighted',
       'driver_min_price_weighted', 'price_way_weighted',
       'price_way_taximeter_weighted', 'waiting_price_taximeter_weighted',
       'paid_cancellation_price_weighted', 'driver_gold_min_price_weighted',
       'driver_silver_min_price_weighted', 'paid_waiting

In [217]:
df.sort_values(by='date_day')

LOCALITY_RK    date_day  DRIVERS   VIEWS  wd  driver_bonus_target_0  \
0          22534  2020-04-01      953   25523   3               0.000000   
1          22534  2020-04-02      950   24682   4               0.000000   
2          22534  2020-04-03      985   26641   5               0.000000   
3          22534  2020-04-04      968   26517   6               0.000000   
4          22534  2020-04-05      900   26855   7               0.000000   
5          22534  2020-04-06     1025   29211   1               0.000000   
6          22534  2020-04-07     1029   26877   2               0.000000   
7          22534  2020-04-08     1034   27613   3               0.000000   
8          22534  2020-04-09     1023   28285   4               0.000000   
9          22534  2020-04-10     1055   34283   5               0.000000   
10         22534  2020-04-11      990   33012   6               0.000000   
11         22534  2020-04-12      886   30545   7               0.000000   
12         22534  2020-04-13     1045   31510   1               0.000000   
13         22534  2020-04-14     1089   30368   2               0.000000   
14         22534  2020-04-15     1096   36657   3             140.000000   
15         22534  2020-04-16     1109   33463   4             140.000000   
16         22534  2020-04-17     1108   33595   5             140.000000   
17         22534  2020-04-18      992   31313   6             140.000000   
18         22534  2020-04-19      822   44153   7             140.000000   
19         22534  2020-04-20      944   41533   1             140.000000   
20         22534  2020-04-21     1019   31492   2             140.000000   
21         22534  2020-04-22     1039   29611   3             140.000000   
22         22534  2020-04-23     1048   29992   4             140.000000   
23         22534  2020-04-24     1073   34179   5             140.000000   
24         22534  2020-04-25      957   36564   6             140.000000   
25         22534  2020-04-26      810   31988   7             120.000000   
26         22534  2020-04-27      985   32241   1             120.000000   
27         22534  2020-04-28     1008   31144   2             120.000000   
28         22534  2020-04-29     1049   32388   3             120.000000   
29         22534  2020-04-30     1021   43154   4             120.000000   
30         22534  2020-05-01      909   37464   5             120.000000   
31         22534  2020-05-02      813   32238   6             120.000000   
32         22534  2020-05-03      799   29971   7             120.000000   
33         22534  2020-05-04      898   28037   1             120.000000   
34         22534  2020-05-05      970   28548   2             120.000000   
35         22534  2020-05-06     1031   31809   3             120.000000   
36         22534  2020-05-07     1004   30894   4             120.000000   
37         22534  2020-05-08     1063   38739   5             120.000000   
38         22534  2020-05-09      916   42934   6             120.000000   
39         22534  2020-05-10      854   43047   7             120.000000   
40         22534  2020-05-11      897   31358   1             120.000000   
41         22534  2020-05-12     1011   38782   2             120.000000   
42         22534  2020-05-13     1025   37145   3             120.000000   
43         22534  2020-05-14     1088   39676   4             120.000000   
44         22534  2020-05-15     1106   42886   5             120.000000   
45         22534  2020-05-16      983   41095   6             120.000000   
46         22534  2020-05-17      856   35426   7             120.000000   
47         22534  2020-05-18     1039   45131   1             120.000000   
48         22534  2020-05-19     1035   35897   2             103.333333   
49         22534  2020-05-20     1057   41060   3             103.333333   
50         22534  2020-05-21     1063   35691   4             103.333333   
51         22534  2020-05-22     1073   41465   5    

In [221]:
df = df[['LOCALITY_RK', 'wd', 'date_day', 'DRIVERS', 'VIEWS',
       'driver_bonus_target_0', 'driver_bonus_target_1',
       'driver_bonus_target_2', 'driver_bonus_payment_0',
       'driver_bonus_payment_1', 'driver_bonus_payment_2',
       'driver_bonus_orders_counted', 'driver_bonus_fraud_counted',
       'driver_bonus_paid_sum', 'mfg_max_fare_gold', 'mfg_max_stair_gold',
       'mfg_max_fare_not_gold', 'mfg_max_stair_not_gold', 'mfg_ORDERS_COUNT',
       'mfg_FEE', 'geomin_DRIVER_MIN_PRICE', 'geomin_CLIENT_EXTRA_CHARGE',
       'min_price_weighted', 'prepaid_time_weighted', 'prepaid_way_weighted',
       'price_time_weighted', 'price_time_taximeter_weighted',
       'free_waiting_time_weighted', 'waiting_price_weighted',
       'driver_min_price_weighted', 'price_way_weighted',
       'price_way_taximeter_weighted', 'waiting_price_taximeter_weighted',
       'paid_cancellation_price_weighted', 'driver_gold_min_price_weighted',
       'driver_silver_min_price_weighted', 'paid_waiting_for_driver_weighted',
       'MAX_USAGE_COUNT', 'MIN_PRICE',
       'MAX_DISCOUNT', 'coupon_tariff_bitmap', 'UNIQUE_COUPONS', 'CI_COUPONS',
       'COUPONS_ORDERS', 'ORDERS', 'RIDES', 'O2R', 'CLIENT_BILL_AMT',
       'CONTRIBUTION']]

In [222]:
df

LOCALITY_RK  wd    date_day  DRIVERS   VIEWS  driver_bonus_target_0  \
0          22534   3  2020-04-01      953   25523               0.000000   
1          22534   4  2020-04-02      950   24682               0.000000   
2          22534   5  2020-04-03      985   26641               0.000000   
3          22534   6  2020-04-04      968   26517               0.000000   
4          22534   7  2020-04-05      900   26855               0.000000   
5          22534   1  2020-04-06     1025   29211               0.000000   
6          22534   2  2020-04-07     1029   26877               0.000000   
7          22534   3  2020-04-08     1034   27613               0.000000   
8          22534   4  2020-04-09     1023   28285               0.000000   
9          22534   5  2020-04-10     1055   34283               0.000000   
10         22534   6  2020-04-11      990   33012               0.000000   
11         22534   7  2020-04-12      886   30545               0.000000   
12         22534   1  2020-04-13     1045   31510               0.000000   
13         22534   2  2020-04-14     1089   30368               0.000000   
14         22534   3  2020-04-15     1096   36657             140.000000   
15         22534   4  2020-04-16     1109   33463             140.000000   
16         22534   5  2020-04-17     1108   33595             140.000000   
17         22534   6  2020-04-18      992   31313             140.000000   
18         22534   7  2020-04-19      822   44153             140.000000   
19         22534   1  2020-04-20      944   41533             140.000000   
20         22534   2  2020-04-21     1019   31492             140.000000   
21         22534   3  2020-04-22     1039   29611             140.000000   
22         22534   4  2020-04-23     1048   29992             140.000000   
23         22534   5  2020-04-24     1073   34179             140.000000   
24         22534   6  2020-04-25      957   36564             140.000000   
25         22534   7  2020-04-26      810   31988             120.000000   
26         22534   1  2020-04-27      985   32241             120.000000   
27         22534   2  2020-04-28     1008   31144             120.000000   
28         22534   3  2020-04-29     1049   32388             120.000000   
29         22534   4  2020-04-30     1021   43154             120.000000   
30         22534   5  2020-05-01      909   37464             120.000000   
31         22534   6  2020-05-02      813   32238             120.000000   
32         22534   7  2020-05-03      799   29971             120.000000   
33         22534   1  2020-05-04      898   28037             120.000000   
34         22534   2  2020-05-05      970   28548             120.000000   
35         22534   3  2020-05-06     1031   31809             120.000000   
36         22534   4  2020-05-07     1004   30894             120.000000   
37         22534   5  2020-05-08     1063   38739             120.000000   
38         22534   6  2020-05-09      916   42934             120.000000   
39         22534   7  2020-05-10      854   43047             120.000000   
40         22534   1  2020-05-11      897   31358             120.000000   
41         22534   2  2020-05-12     1011   38782             120.000000   
42         22534   3  2020-05-13     1025   37145             120.000000   
43         22534   4  2020-05-14     1088   39676             120.000000   
44         22534   5  2020-05-15     1106   42886             120.000000   
45         22534   6  2020-05-16      983   41095             120.000000   
46         22534   7  2020-05-17      856   35426             120.000000   
47         22534   1  2020-05-18     1039   45131             120.000000   
48         22534   2  2020-05-19     1035   35897             103.333333   
49         22534   3  2020-05-20     1057   41060             103.333333   
50         22534   4  2020-05-21     1063   35691             103.333333   
51         22534   5  2020-05-22     1073   41465    

In [223]:
#C.import_from_pandas(df, ('SANDBOX', 'all_x_all_data'))

In [6]:
test_sql = '''
select min(dt)
from surge_statistic.surge_20_data s
       join exasol_mart.tariff t on toUInt64(s.tariff_id) = toUInt64(t.tariff_rk)
where 1 = 1
    and date >= toDate('2020-05-01') and date <= toDate('2021-12-08')
    and t.locality_rk = 22534
    and t.tariff_group_rk in (2, 3, 4, 5)
'''

In [8]:
test = clickhouse_vip.fetch(test_sql)

In [9]:
test

min(dt)
0 2021-01-21 16:55:00

Days od Week Pricing

In [ ]:
list_of_vals = [2**(i) for i in range(7)]
dict_of_vals = dict((v,k+1) for k,v in dict(list(enumerate(list_of_vals))).items())

all_combinations = []
for r in range(len(list_of_vals) + 1):
    combinations_object = itertools.combinations(list_of_vals, r)
    combinations_list = list(combinations_object)
    all_combinations += combinations_list

In [ ]:
days_of_week = {}
for i in all_combinations:
    v = []
    for ii in i:
        v.append(dict_of_vals.get(ii))
    days_of_week.update({sum(i):v})

In [ ]:
for i in [15, 16, 30, 31, 60, 67, 96, 97, 127]:
    print(i, days_of_week.get(i))